In [181]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler,StandardScaler
from keras.callbacks import ModelCheckpoint


In [2]:
merged = pd.read_csv(r'C:\Users\jerin\Downloads\lbnlbldg59\lbnlbldg59\lbnlbldg59.processed\LBNLBLDG59\clean_Bldg59_2018to2020\clean data\long_merge.csv')

zone = "47"

if zone in ["36", "37", "38", "39", "40", "41", "42", "64", "65", "66", "67", "68", "69", "70"]:
    rtu = "rtu_001"
    wing = "hvac_N"
elif zone in ["18", "25", "26", "45", "48", "55", "56", "61"]:
    rtu = "rtu_003"
    wing = "hvac_S"
elif zone in ["16", "17", "21", "22", "23", "24", "46", "47", "51", "52", "53", "54"]:
    rtu = "rtu_004"
    wing = "hvac_S"
else:
    rtu = "rtu_002"
    wing = "hvac_N"
#merged is the dataframe
sorted = merged[["date"]+[col for col in merged.columns if zone in col or rtu in col or wing in col]+["hp_hws_temp", "aru_001_cwr_temp" , "aru_001_cws_fr_gpm" ,"aru_001_cws_temp","aru_001_hwr_temp" ,"aru_001_hws_fr_gpm" ,"aru_001_hws_temp"]]
sorted

date  zone_047_hw_valve  rtu_004_sat_sp_tn  \
0        2018-01-01 00:00:00              100.0               69.0   
1        2018-01-01 00:01:00              100.0               69.0   
2        2018-01-01 00:02:00              100.0               69.0   
3        2018-01-01 00:03:00              100.0               69.0   
4        2018-01-01 00:04:00              100.0               69.0   
...                      ...                ...                ...   
2072149  2020-12-31 23:58:00              100.0               68.0   
2072150  2020-12-31 23:58:00              100.0               68.0   
2072151  2020-12-31 23:59:00              100.0               68.0   
2072152  2020-12-31 23:59:00              100.0               68.0   
2072153  2021-01-01 00:00:00              100.0               68.0   

         zone_047_temp  zone_047_fan_spd  rtu_004_fltrd_sa_flow_tn  \
0                 67.5              20.0                  9265.604   
1                 67.5              20.0                  9265.604   
2                 67.5              20.0                  9708.240   
3                 67.5              20.0                  9611.638   
4                 67.5              20.0                  9215.110   
...                ...               ...                       ...   
2072149           63.2              20.0                 18884.834   
2072150           63.2              20.0                 18884.834   
2072151           63.2              20.0                 19345.508   
2072152           63.2              20.0                 19345.508   
2072153           63.2              20.0                 18650.232   

         rtu_004_sa_temp  rtu_004_pa_static_stpt_tn  rtu_004_oa_flow_tn  \
0                   66.1                       0.06            0.000000   
1                   66.0                       0.06         6572.099162   
2                   66.1                       0.06         7628.832542   
3                   66.1                       0.06         7710.294617   
4                   66.0                       0.06         7139.184090   
...                  ...                        ...                 ...   
2072149             64.4                       0.06         2938.320000   
2072150             64.4                       0.06         2938.320000   
2072151             64.3                       0.06         3154.390000   
2072152             64.3                       0.06         3154.390000   
2072153             64.1                       0.06         3076.270000   

         rtu_004_oadmpr_pct  ...  zone_047_heating_sp  Unnamed: 47_y  \
0                      28.0  ...                  NaN            NaN   
1                      28.0  ...                  NaN            NaN   
2                      28.0  ...                  NaN            NaN   
3                      28.0  ...                  NaN            NaN   
4                      28.0  ...                  NaN            NaN   
...                     ...  ...                  ...            ...   
2072149                23.4  ...                 71.0           69.0   
2072150                23.4  ...                 71.0           69.0   
2072151                23.4  ...                 71.0           69.0   
2072152                23.4  ...                 71.0           69.0   
2072153                22.9  ...                 71.0           69.0   

            hvac_S  hp_hws_temp  aru_001_cwr_temp  aru_001_cws_fr_gpm  \
0              NaN         75.3               NaN                 NaN   
1              NaN         75.3               NaN                 NaN   
2              NaN         75.3               NaN                 NaN   
3              NaN         75.3               NaN                 NaN   
4              NaN         75.3               NaN                 NaN   
...            ...          ...               ...                 ...   
2072149  23.145000        123.8             56.25               5

In [7]:
final_df = sorted.copy()
final_df['date'] = pd.to_datetime(final_df['date'], format = "%Y-%m-%d %H:%M:%S")
final_df = final_df[ (final_df.date.dt.date >date(2019, 4, 1)) & (final_df.date.dt.date< date(2020, 2, 15))]
final_df.isna().sum()

date                                          0
zone_047_hw_valve                             0
rtu_004_sat_sp_tn                             0
zone_047_temp                                 0
zone_047_fan_spd                              0
rtu_004_fltrd_sa_flow_tn                      0
rtu_004_sa_temp                               0
rtu_004_pa_static_stpt_tn                     0
rtu_004_oa_flow_tn                            0
rtu_004_oadmpr_pct                            0
rtu_004_econ_stpt_tn                          0
rtu_004_ra_temp                               0
rtu_004_oa_temp                               0
rtu_004_ma_temp                               0
rtu_004_sf_vfd_spd_fbk_tn                     0
rtu_004_rf_vfd_spd_fbk_tn                     0
rtu_004_fltrd_gnd_lvl_plenum_press_tn         0
rtu_004_fltrd_lvl2_plenum_press_tn            0
zone_047_cooling_sp                           0
Unnamed: 47_x                            394570
zone_047_heating_sp                     

In [4]:
testdataset_df = final_df[(final_df.date.dt.date <date(2019, 11, 8))]

traindataset_df = final_df[ (final_df.date.dt.date >date(2019, 11, 8))]

testdataset = testdataset_df[['rtu_004_oa_temp','rtu_004_ra_temp','hp_hws_temp','rtu_004_oa_flow_tn','rtu_004_oadmpr_pct',
                    'rtu_004_sat_sp_tn','rtu_004_rf_vfd_spd_fbk_tn','rtu_004_ma_temp','rtu_004_sa_temp','rtu_004_fltrd_sa_flow_tn',
                    'rtu_004_sf_vfd_spd_fbk_tn']].values


traindataset = traindataset_df[['rtu_004_oa_temp','rtu_004_ra_temp','hp_hws_temp','rtu_004_oa_flow_tn','rtu_004_oadmpr_pct',
                    'rtu_004_sat_sp_tn','rtu_004_rf_vfd_spd_fbk_tn','rtu_004_ma_temp','rtu_004_sa_temp','rtu_004_fltrd_sa_flow_tn',
                    'rtu_004_sf_vfd_spd_fbk_tn']].values

In [5]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')


scaler = MinMaxScaler(feature_range=(0, 1))
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [47]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x1,x2,x3,x4,x5,x6,x7,x8,x9,Y = [],[],[],[],[],[],[],[],[],[]
    for i in range(len(dataset)-time_step-1):
        x1.append(dataset[i:(i+time_step), 0])
        x2.append(dataset[i:(i+time_step), 1])
        x3.append(dataset[i:(i+time_step), 2])
        x4.append(dataset[i:(i+time_step), 3])
        x5.append(dataset[i:(i+time_step), 4])
        x6.append(dataset[i:(i+time_step), 5])
        x7.append(dataset[i:(i+time_step), 6])
        x8.append(dataset[i:(i+time_step), 7])
        # x9.append(dataset[i:(i+time_step), 8])
        Y.append([dataset[i + time_step, 7]])
    x1,x2,x3,x4,x5,x6,x7,x8 =  np.array(x1),np.array(x2),np.array(x3), np.array(x4),np.array(x5),np.array(x6),np.array(x7),np.array(x8)#,np.array(x9)
    Y = np.reshape(Y,(len(Y),1))
    return np.stack([x1,x2,x3,x4,x5,x6,x7,x8],axis=2),Y




time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=1))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm2.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=10, batch_size=64, verbose=1, callbacks=[checkpoint_callback])


c:\Users\jerin\anaconda3\envs\smartbuilding\Lib\site-packages\keras\src\layers\rnn\rnn.py:205: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/10
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0071
Epoch 1: val_loss improved from inf to 0.01145, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 77s 23ms/step - loss: 0.0071 - val_loss: 0.0115
Epoch 2/10
3217/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0013
Epoch 2: val_loss improved from 0.01145 to 0.01144, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 73s 23ms/step - loss: 0.0013 - val_loss: 0.0114
Epoch 3/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0010
Epoch 3: val_loss improved from 0.01144 to 0.00729, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 71s 22ms/step - loss: 0.0010 - val_loss: 0.0073
Epoch 4/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 5.5876e-04
Epoch 4: val_loss improved from 0.00729 to 0.00409, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 73s 23ms/step - loss: 5.5871e-04 - val_loss: 0.0041
Epoch 5/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 3.9261e-04
Epoch 

In [45]:
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - loss: 1.8977e-04
Epoch 1: val_loss improved from inf to 0.01131, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 94s 29ms/step - loss: 1.8977e-04 - val_loss: 0.0113
Epoch 2/5
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 1.7357e-04
Epoch 2: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 91s 28ms/step - loss: 1.7358e-04 - val_loss: 0.0123
Epoch 3/5
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 1.6701e-04
Epoch 3: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 92s 28ms/step - loss: 1.6701e-04 - val_loss: 0.0127
Epoch 4/5
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 1.7043e-04
Epoch 4: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 91s 28ms/step - loss: 1.7043e-04 - val_loss: 0.0131
Epoch 5/5
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - loss: 1.6319e-04
Epoch 5: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 104s 32m

In [48]:
# train_predict = model.predict(X_train)
test_predict = model.predict(X_test)

9900/9900 ━━━━━━━━━━━━━━━━━━━━ 34s 3ms/step


In [49]:
%matplotlib qt
#'rtu_004_ma_temp','rtu_004_sa_temp'
var = 0
plt.plot(testdataset_df['date'][31:],y_test, label='Original Testing Data', color='blue')
plt.plot(testdataset_df['date'][31:],test_predict, label='Predicted Testing Data', color='red',alpha=0.8)
# anomalies = np.where(abs(test_predict[:,var] - y_test[:,var]) > 0.38)[0]
# plt.scatter(anomalies,test_predict[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [50]:
from tensorflow.keras.models import load_model
# model.save("MA_temp_model.h5") 
# loaded_model = load_model("MA_temp_model.h5")

ENERGY DATA

In [19]:
zone =  ["18", "25", "26", "45", "48", "55", "56", "61","16", "17", "21", "23", "24", "46", "47", "51", "52", "53", "54"]
rtu = ["rtu_001","rtu_002","rtu_003","rtu_004"]
wing = ["hvac_N","hvac_S"]
env = ["air_temp_set_1","air_temp_set_2","dew_point_temperature_set_1d","relative_humidity_set_1","solar_radiation_set_1"]
wifi=["wifi_third_south","wifi_fourth_south"]
# any(sub in col for sub in zone) or
energy_data = merged[["date"]+[col for col in merged.columns if 
                               any(sub in col for sub in env) or any(sub in col for sub in wifi)]+wing]
df_filtered = energy_data[[col for col in energy_data.columns if 'Unnamed' not in col]]
df_filtered = df_filtered[[col for col in df_filtered.columns if 'co2' not in col]]
df_filtered = df_filtered[[col for col in df_filtered.columns if 'templogger' not in col]]
# df_filtered = df_filtered.dropna()
df_filtered.head(2)

date  air_temp_set_1  air_temp_set_2  \
0  2018-01-01 00:00:00           11.64           11.51   
1  2018-01-01 00:01:00           11.64           11.51   

   dew_point_temperature_set_1d  relative_humidity_set_1  \
0                           8.1                    79.07   
1                           8.1                    79.07   

   solar_radiation_set_1  wifi_third_south  wifi_fourth_south  hvac_N  hvac_S  
0                   86.7               NaN                NaN     NaN     NaN  
1                   86.7               NaN                NaN     NaN     NaN

In [20]:
df_filtered['date'] = pd.to_datetime(df_filtered['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = df_filtered[ (df_filtered.date.dt.date >date(2019, 4, 1)) & (df_filtered.date.dt.date< date(2020, 2, 15))]
# df_filtered.isna().sum()
if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

There are NA values in the DataFrame columns.


In [21]:
testdataset_df = df_filtered[(df_filtered.date.dt.date <date(2019, 8, 21))]

traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]

testdataset = testdataset_df.drop(columns=["date"]).values

traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [22]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = MinMaxScaler(feature_range=(0, 1))
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [26]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = [[] for _ in range(9)] 
    Y = []
    for i in range(len(dataset) - time_step - 1):
        for j in range(9):
            x[j].append(dataset[i:(i + time_step), j])
        Y.append([dataset[i + time_step, 7],dataset[i + time_step, 8]])
    x= [np.array(feature_list) for feature_list in x]
    Y = np.reshape(Y,(len(Y),2))
    return np.stack(x,axis=2),Y

time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=2))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm_energy_01.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=3, batch_size=64, verbose=1, callbacks=[checkpoint_callback])


Epoch 1/3
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0036
Epoch 1: val_loss improved from inf to 0.00068, saving model to lstm_energy_01.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 65s 20ms/step - loss: 0.0036 - val_loss: 6.8049e-04
Epoch 2/3
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 4.8055e-04
Epoch 2: val_loss improved from 0.00068 to 0.00064, saving model to lstm_energy_01.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 60s 19ms/step - loss: 4.8055e-04 - val_loss: 6.4225e-04
Epoch 3/3
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 4.6623e-04
Epoch 3: val_loss improved from 0.00064 to 0.00061, saving model to lstm_energy_01.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 61s 19ms/step - loss: 4.6622e-04 - val_loss: 6.0579e-04


In [18]:
# checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
# model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=10, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

In [27]:
test_predict1 = model.predict(X_test)
# train_predict1 = model.predict(X_train)

6345/6345 ━━━━━━━━━━━━━━━━━━━━ 22s 3ms/step


In [30]:
%matplotlib qt
var = 1
plt.plot(testdataset_df['date'][31:],y_test[:,1], label='Original Testing Data', color='blue')
plt.plot(testdataset_df['date'][31:],test_predict1[:,1], label='Predicted Testing Data', color='red',alpha=0.8)
# anomalies = np.where(abs(test_predict[:,var] - y_test[:,var]) > 0.38)[0]
# plt.scatter(anomalies,test_predict[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [31]:
# from tensorflow.keras.models import load_model
# model.save("energy_model_01.h5") 

In [8]:
%matplotlib qt
plt.plot(df_filtered['date'],df_filtered['hvac_S'])
plt.plot(df_filtered['date'],df_filtered['rtu_003_sf_vfd_spd_fbk_tn'])
plt.plot(df_filtered['date'],df_filtered['zone_025_temp'])

In [22]:
plt.plot(merged['hvac_S'])
plt.plot(testdataset_df['hvac_S'])
plt.plot(traindataset_df['hvac_S'],'r')

In [24]:
plt.plot(merged['hvac_N'])
plt.plot(testdataset_df['hvac_N'])
plt.plot(traindataset_df['hvac_N'],'r')

In [32]:
# merged.columns.to_list()

2.16.1


LSTM 2.0

In [39]:
rtu = ["rtu_003"]
# wing = ["hvac_N","hvac_S"]
env = ["air_temp_set_1","air_temp_set_2","dew_point_temperature_set_1d","relative_humidity_set_1","solar_radiation_set_1"]
wifi=["wifi_third_south","wifi_fourth_south"]
["rtu_003_ma_temp",]
# any(sub in col for sub in zone) or
energy_data = merged[["date","hp_hws_temp"]+[col for col in merged.columns if 
                               any(sub in col for sub in rtu) or any(sub in col for sub in wifi)]+env]
df_filtered = energy_data[[col for col in energy_data.columns if 'Unnamed' not in col]]
df_filtered = df_filtered[[col for col in df_filtered.columns if 'co2' not in col]]
df_filtered = df_filtered[[col for col in df_filtered.columns if 'templogger' not in col]]
# df_filtered = df_filtered.dropna()
df_filtered.head(2)

date  hp_hws_temp  rtu_003_sat_sp_tn  \
0  2018-01-01 00:00:00         75.3               65.0   
1  2018-01-01 00:01:00         75.3               65.0   

   rtu_003_fltrd_sa_flow_tn  rtu_003_sa_temp  rtu_003_pa_static_stpt_tn  \
0                 13558.539             65.5                        0.6   
1                 13592.909             65.6                        0.6   

   rtu_003_oa_flow_tn  rtu_003_oadmpr_pct  rtu_003_econ_stpt_tn  \
0            0.000000                34.6                  65.0   
1         5992.059572                34.6                  65.0   

   rtu_003_ra_temp  ...  rtu_003_rf_vfd_spd_fbk_tn  \
0             67.9  ...                       49.9   
1             67.9  ...                       49.4   

   rtu_003_fltrd_gnd_lvl_plenum_press_tn  rtu_003_fltrd_lvl2_plenum_press_tn  \
0                                   0.04                                0.05   
1                                   0.04                                0.04   

   wifi_third_south  wifi_fourth_south  air_temp_set_1  air_temp_set_2  \
0               NaN                NaN           11.64           11.51   
1               NaN                NaN           11.64           11.51   

   dew_point_temperature_set_1d  relative_humidity_set_1  \
0                           8.1                    79.07   
1                           8.1                    79.07   

   solar_radiation_set_1  
0                   86.7  
1                   86.7  

[2 rows x 23 columns]

In [40]:
df_filtered['date'] = pd.to_datetime(df_filtered['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = df_filtered[ (df_filtered.date.dt.date >date(2019, 4, 1)) & (df_filtered.date.dt.date< date(2020, 2, 15))]
# df_filtered.isna().sum()
if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

In [68]:
df_filtered = df_filtered.loc[:,['date','hp_hws_temp',
 'rtu_003_sa_temp',
 'rtu_003_oadmpr_pct',
 'rtu_003_ra_temp',
 'rtu_003_oa_temp',
 'rtu_003_ma_temp',
 'rtu_003_sf_vfd_spd_fbk_tn',
 'rtu_003_rf_vfd_spd_fbk_tn','wifi_third_south',
 'wifi_fourth_south',
 'air_temp_set_1',
 'air_temp_set_2',
 'dew_point_temperature_set_1d',
 'relative_humidity_set_1',
 'solar_radiation_set_1']]

In [188]:
testdataset_df = df_filtered[(df_filtered.date.dt.date <date(2019, 8, 21))]

traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]
# .ewm(com = 1000,adjust=True).mean()
testdataset = testdataset_df.drop(columns=["date"]).values

traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [189]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = StandardScaler()
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [191]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = [[] for _ in range(15)] 
    Y = []
    for i in range(len(dataset) - time_step - 1):
        for j in range(15):
            x[j].append(dataset[i:(i + time_step), j])
        Y.append([dataset[i + time_step, 0],dataset[i + time_step, 1],dataset[i + time_step, 2],dataset[i + time_step, 3],dataset[i + time_step, 4],dataset[i + time_step, 5],
                  dataset[i + time_step, 6],dataset[i + time_step, 7]])
    x= [np.array(feature_list) for feature_list in x]
    Y = np.reshape(Y,(len(Y),8))
    return np.stack(x,axis=2),Y

time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=8))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm_smooth_01.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5


c:\Users\jerin\anaconda3\envs\smartbuilding\Lib\site-packages\keras\src\layers\rnn\rnn.py:205: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


3217/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.1413
Epoch 1: val_loss improved from inf to 0.52256, saving model to lstm_smooth_01.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 66s 20ms/step - loss: 0.1412 - val_loss: 0.5226
Epoch 2/5
3217/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0393
Epoch 2: val_loss improved from 0.52256 to 0.50228, saving model to lstm_smooth_01.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 65s 20ms/step - loss: 0.0393 - val_loss: 0.5023
Epoch 3/5
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0347
Epoch 3: val_loss improved from 0.50228 to 0.48711, saving model to lstm_smooth_01.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 65s 20ms/step - loss: 0.0347 - val_loss: 0.4871
Epoch 4/5
3217/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0319
Epoch 4: val_loss did not improve from 0.48711
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 66s 20ms/step - loss: 0.0319 - val_loss: 0.4958
Epoch 5/5
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0303
Epoch 5: val_loss did not improve from 

In [192]:
test_predict1 = model.predict(X_test)

6345/6345 ━━━━━━━━━━━━━━━━━━━━ 23s 4ms/step


In [193]:
%matplotlib qt
var = 0
plt.plot(y_test[:,var], label='Original Testing Data', color='blue')
plt.plot(test_predict1[:,var], label='Predicted Testing Data', color='red',alpha=0.8)
anomalies = np.where(abs(test_predict1[:,var] - y_test[:,var]) > 0.38)[var]
plt.scatter(anomalies,test_predict1[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [176]:
var = 0
plt.plot((test_predict1 - y_test)[:,var])

In [72]:
params = ['hp_hws_temp',
 'rtu_003_sa_temp',
 'rtu_003_oadmpr_pct',
 'rtu_003_ra_temp',
 'rtu_003_oa_temp',
 'rtu_003_ma_temp',
 'rtu_003_sf_vfd_spd_fbk_tn',
 'rtu_003_rf_vfd_spd_fbk_tn','wifi_third_south',
 'wifi_fourth_south',
 'air_temp_set_1',
 'air_temp_set_2',
 'dew_point_temperature_set_1d',
 'relative_humidity_set_1',
 'solar_radiation_set_1']

idx_2_params = {}
for i, param in enumerate(params):
    idx_2_params[i] = param

In [73]:
idx_2_params

{0: 'hp_hws_temp',
 1: 'rtu_003_sa_temp',
 2: 'rtu_003_oadmpr_pct',
 3: 'rtu_003_ra_temp',
 4: 'rtu_003_oa_temp',
 5: 'rtu_003_ma_temp',
 6: 'rtu_003_sf_vfd_spd_fbk_tn',
 7: 'rtu_003_rf_vfd_spd_fbk_tn',
 8: 'wifi_third_south',
 9: 'wifi_fourth_south',
 10: 'air_temp_set_1',
 11: 'air_temp_set_2',
 12: 'dew_point_temperature_set_1d',
 13: 'relative_humidity_set_1',
 14: 'solar_radiation_set_1'}

KMEANS

In [194]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA
# Generating random data for demonstration
np.random.seed(0)
X = test_predict1 - y_test

pca = PCA(n_components=2)
X = pca.fit_transform(X)


k = 3

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)

# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5, edgecolors='k')
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [109]:
plt.plot((test_predict1 - y_test)[:,2])

In [77]:
pca.components_

array([[ 5.8607887e-02, -2.4713947e-01,  2.4978706e-01, -7.8289807e-01,
        -2.0218764e-01, -2.8860569e-01,  2.7817219e-01,  2.4209845e-01],
       [-2.6845999e-02,  1.2596852e-01,  9.6294099e-01,  2.0099232e-01,
         3.3391420e-02,  7.7613303e-04, -7.1204931e-02, -9.7836025e-02]],
      dtype=float32)

In [204]:
k = 60
X= test_predict1 - y_test
processed_data = []
feat_df = pd.DataFrame(columns=["mean","std",])
for i in range(0,len(X), 30 ):
    mean = X[i:i+k].mean(axis = 0)
    std = X[i:i+k].std(axis = 0)
    max = X[i:i+k].max(axis = 0)
    min = X[i:i+k].min(axis = 0)
    iqr = np.percentile(X[i:i+k], 75, axis=0) - np.percentile(X[i:i+k], 25,axis=0)
    data = np.concatenate([mean, std, max, min, iqr])
    processed_data.append([data])
processed_data = np.concatenate(processed_data,axis=0) 

In [197]:
X = processed_data

pca = PCA(n_components=2)
X = pca.fit_transform(X)


k = 4

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)

# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [167]:

dd = df_filtered.drop(columns=["date"],inplace=False)
dg = dd.ewm(com = 1000,adjust=True).mean()

In [168]:
df_filtered

date  hp_hws_temp  rtu_003_sa_temp  rtu_003_oadmpr_pct  \
555845  2019-04-02 00:00:00        120.7             66.7                84.4   
555846  2019-04-02 00:01:00        120.4             65.8                85.4   
555847  2019-04-02 00:02:00        120.1             65.1                66.2   
555848  2019-04-02 00:03:00        119.6             64.9                56.0   
555849  2019-04-02 00:04:00        119.3             65.5                54.6   
...                     ...          ...              ...                 ...   
1080190 2020-02-14 23:57:00        121.9             67.3                52.8   
1080191 2020-02-14 23:58:00        122.7             69.2                64.8   
1080192 2020-02-14 23:58:00        122.7             69.2                64.8   
1080193 2020-02-14 23:59:00        122.9             68.7                80.8   
1080194 2020-02-14 23:59:00        122.9             68.7                80.8   

         rtu_003_ra_temp  rtu_003_oa_temp  rtu_003_ma_temp  \
555845              72.2             59.2             66.7   
555846              72.2             59.5             65.0   
555847              72.1             59.4             64.0   
555848              72.2             59.4             65.7   
555849              72.0             59.2             67.1   
...                  ...              ...              ...   
1080190             73.2             63.5             69.2   
1080191             73.3             63.4             70.0   
1080192             73.3             63.4             70.0   
1080193             73.3             63.1             67.3   
1080194             73.3             63.1             67.3   

         rtu_003_sf_vfd_spd_fbk_tn  rtu_003_rf_vfd_spd_fbk_tn  \
555845                        79.6                       53.7   
555846                        78.1                       54.4   
555847                        78.0                       60.1   
555848                        79.1                       55.5   
555849                        75.2                       53.1   
...                            ...                        ...   
1080190                       80.9                       61.3   
1080191                       81.0                       53.8   
1080192                       81.0                       53.8   
1080193                       82.2                       60.1   
1080194                       82.2                       60.1   

         wifi_third_south  wifi_fourth_south  air_temp_set_1  air_temp_set_2  \
555845               34.0               31.0           15.67           14.92   
555846               34.0               31.0           15.67           14.92   
555847               34.0               31.0           15.67           14.92   
555848               34.0               31.0           15.67           14.92   
555849               34.0               31.0           15.67           14.92   
...                   ...                ...             ...             ...   
1080190               0.0                0.0           16.42           13.93   
1080191               0.0                0.0           16.42           13.93   
1080192               0.0                0.0           16.42           13.93   
1080193               0.0                0.0           16.42           13.93   
1080194               0.0                0.0           16.42           13.93   

         dew_point_temperature_set_1d  relative_humidity_set_1  \
555845                          11.77                    77.80   
555846                          11.77                    77.80   
555847                          11.77                    77.80   
555848                          11.77                    77.80   
555849                          11.77                    77.80   
...                               ...                      ...   
1080190                          6.93                    53.66   
1080191                          6.

In [170]:
plt.plot(dd["hp_hws_temp"])
plt.plot(dg["hp_hws_temp"])

In [202]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt

# Generating random data for demonstration
np.random.seed(0)
X = processed_data

# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2)

# Fitting the model to the data
gmm.fit(X)

# Getting the cluster labels
labels = gmm.predict(X)

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()
